In [26]:
from genepy.utils import helper as h

from taigapy import TaigaClient
from celligner import Celligner
tc = TaigaClient()
from bokeh.plotting import output_notebook
from depmapomics import tracker as track
#autoreload
%load_ext autoreload
%autoreload 2
output_notebook()

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


Loading BokehJS ...

In [2]:
# load from taiga public (figshare link)
# load internal expression,
CCLE_expression = tc.get(name='internal-21q3-fe4c',
                         file='CCLE_expression_full')  # https://depmap.org/portal/download/
# load  TCGA expression
# this dataset was generated from  ,using this script: 
# caan be found here:
TCGA_expression = tc.get(name='celligner-input-9827',
                         file='tumor_expression')

No dataset version provided. Using version 16.
No dataset version provided. Using version 1.


In [3]:
# subset gene names to ensembl ids only
CCLE_expression = CCLE_expression[CCLE_expression.columns[:-92]]
CCLE_expression.columns = list(map(lambda x: x.split(
    ' (')[1][:-1] if ' (' in x else x, CCLE_expression.columns))

common = set(CCLE_expression.columns).intersection(
    set(TCGA_expression.columns))
CCLE_expression = CCLE_expression[list(common)]
TCGA_expression = TCGA_expression[list(common)]

In [4]:
# loading annotations
CCLE_annotation = track.getTracker() # the function uses pygsheets to load this: https://docs.google.com/spreadsheets/d/1Pgb5fIClGnErEqzxpU7qqX6ULpGTDjvzWwDN8XUJKIY/edit#gid=746987867 
TCGA_annotation = tc.get(name='celligner-input-9827',
                         file='tumor_annotations') # generated manually, found also here: 

No dataset version provided. Using version 1.


In [5]:
# transforming annotations
CCLE_annotation = CCLE_annotation.drop_duplicates('arxspan_id').set_index("arxspan_id")
CCLE_annotation = CCLE_annotation.loc[CCLE_expression.index, ["origin", 'subtype']].rename(columns={"origin": "tissue_type", "subtype": 'disease_type'})
CCLE_annotation["cell_type"] = "cancer cell line"

TCGA_annotation = TCGA_annotation.set_index("sampleID").loc[TCGA_expression.index,["lineage",
"subtype"]].rename(columns={"lineage":"tissue_type", "subtype": 'disease_type'})
TCGA_annotation['cell_type'] = "tumor sample"

In [6]:
my_alligner = Celligner(snn_kwargs={"neighbor_num": 30, "min_shared_neighbor_proportion": 1/15,}, make_plots=True)

my_alligner.fit(TCGA_expression, TCGA_annotation)

fetching gene names from biomart cache
using only usefull genes
looking at 12236 samples.
found 29593 common genes
creating a fit dataset..
reducing dimensionality...
clustering...
         Falling back to preprocessing with `sc.pp.pca` and default params.


doing differential expression analysis on the clusters
running differential expression on 58 clusters
running limmapy on the samples
you need to have R installed with the limma library installed
3.2.1
done


In [23]:
# mnn
my_alligner.method = "mnn"
my_alligner.mnn_kwargs = {
  "var_adj": True,
  "svd_mode": "rsvd",
  "svd_dim": None,
  "k1": 50,
  "k2": 5
}
my_alligner.transform(CCLE_expression, CCLE_annotation)

looking at 1411 samples.
found 29593 common genes
creating a transform input..
reducing dimensionality...
clustering..
         Falling back to preprocessing with `sc.pp.pca` and default params.


doing differential expression analysis on the clusters..
running differential expression on 38 clusters
running limmapy on the samples
you need to have R installed with the limma library installed
3.2.1
there is 0.213 overlap between the fit and transform dataset in their most variable genes
doing cPCA..
transform
regressing out the cPCA components..
doing the MNN analysis using scanPy MNN...
Performing cosine normalization...
Starting MNN correct iteration. Reference batch: 0
Step 1 of 1: processing batch 1
  Looking for MNNs...
  Computing correction vectors...
  Adjusting variance...
  Applying correction...
MNN correction complete. Gathering output...
done
reducing dimensionality...
making plot...


(            ENSG00000271464  ENSG00000162604  ENSG00000065717  \
 ACH-001113         0.000006         0.013362        -0.002096   
 ACH-001289         0.000006         0.011719         0.004035   
 ACH-001339         0.000012         0.011437        -0.004286   
 ACH-001538         0.000010         0.010706        -0.005669   
 ACH-000242         0.000007         0.008742         0.004916   
 ...                     ...              ...              ...   
 ACH-000750         0.000006         0.010134        -0.004264   
 ACH-000285         0.000006         0.011551        -0.003878   
 ACH-001858         0.000011         0.011398        -0.006994   
 ACH-001997         0.000011         0.010609        -0.001055   
 ACH-000052         0.000007         0.010467         0.003477   
 
             ENSG00000203926  ENSG00000256310  ENSG00000254266  \
 ACH-001113         0.000322         0.000115         0.000025   
 ACH-001289         0.000207         0.000115         0.000020   
 ACH-001

In [28]:
# mnn inversed
my_alligner.method = "mnn"
my_alligner.mnn_kwargs = {
  "var_adj": True,
  "svd_mode": "rsvd",
  "svd_dim": None,
  "k1": 5,
  "k2": 50,
}
my_alligner.transform(CCLE_expression, CCLE_annotation)

looking at 1411 samples.
found 29593 common genes
creating a transform input..
reducing dimensionality...
clustering..
         Falling back to preprocessing with `sc.pp.pca` and default params.


doing differential expression analysis on the clusters..
running differential expression on 38 clusters
running limmapy on the samples
you need to have R installed with the limma library installed
3.2.1
there is 0.212 overlap between the fit and transform dataset in their most variable genes
doing cPCA..
transform
regressing out the cPCA components..
doing the MNN analysis using scanPy MNN...
Performing cosine normalization...
Starting MNN correct iteration. Reference batch: 0
Step 1 of 1: processing batch 1
  Looking for MNNs...
  Computing correction vectors...
  Adjusting variance...
  Applying correction...
MNN correction complete. Gathering output...
done
reducing dimensionality...
making plot...


(            ENSG00000271464  ENSG00000162604  ENSG00000065717  \
 ACH-001113        -0.000022         0.011308        -0.001974   
 ACH-001289        -0.000034         0.009161        -0.000861   
 ACH-001339        -0.000026         0.011729         0.004198   
 ACH-001538        -0.000033         0.011291        -0.001481   
 ACH-000242        -0.000029         0.009840         0.001030   
 ...                     ...              ...              ...   
 ACH-000750        -0.000028         0.012118         0.005395   
 ACH-000285        -0.000027         0.009061        -0.004044   
 ACH-001858        -0.000026         0.009738         0.001607   
 ACH-001997        -0.000031         0.011464         0.000256   
 ACH-000052        -0.000025         0.009941        -0.000669   
 
             ENSG00000203926  ENSG00000256310  ENSG00000254266  \
 ACH-001113         0.001567        -0.000019        -0.000165   
 ACH-001289         0.000416        -0.000064        -0.000599   
 ACH-001

In [31]:
my_alligner.plot(color_column="tissue_type", _rerun=False)

reducing dimensionality...
making plot...


In [32]:
# marioni inverse
my_alligner.method = "mnn_marioni"
my_alligner.mnn_kwargs = {
  "k1":5,
  "k2":50,
  "fk": 20,
  "ndist": 3,
}
my_alligner.transform(CCLE_expression, CCLE_annotation)

looking at 1411 samples.
found 29593 common genes
creating a transform input..
reducing dimensionality...
clustering..
         Falling back to preprocessing with `sc.pp.pca` and default params.


doing differential expression analysis on the clusters..
running differential expression on 38 clusters
running limmapy on the samples
you need to have R installed with the limma library installed
3.2.1
there is 0.212 overlap between the fit and transform dataset in their most variable genes
doing cPCA..
transform
regressing out the cPCA components..
doing the MNN analysis using Marioni et al. method..
Performing cosine normalization...
  Looking for MNNs...
done
reducing dimensionality...
> /home/jeremie/celligner/celligner/__init__.py(616)plot()
    615           import ipdb; ipdb.set_trace()
--> 616           col = { l: i for i, l in enumerate(set(annotations[color_column]))}
    617           plot_kwargs.update({'colors':[col[x] for x in annotations[color_column].tolist()]})

ipdb> c
making plot...


IndexError: list index out of range

In [12]:
my_alligner.save('temp/demo/')

In [6]:
my_alligner = Celligner(snn_kwargs={"neighbor_num": 30, "min_shared_neighbor_proportion": 1/15,}, make_plots=True)
my_alligner.load('temp/demo/')

fetching gene names from biomart cache
using only usefull genes


In [21]:
my_alligner.plot(color_column="tissue_type")

reducing dimensionality...
